
## Using SC Navigator result data for analysis and visualization in (Azure) Databricks

This notebook is an example and shows how to get data from SC Navigator into Databricks for further analysis and reporting. This example was build using Databricks Runtime version 13.3 but should work with every newer version. We used the Microsoft examples from [this link](https://learn.microsoft.com/en-us/azure/storage/blobs/data-lake-storage-directory-file-acl-python?tabs=azure-ad) to make this notebook.

#### Does this example also work outside of Databricks?
This jupyter notebook may also work as is on your computer if you have your python environment configured and installed the required packages.

#### Prerequisites
1. Before you run this notebook you need access to the storage of you SC Navigator account. You need to generate a SAS key and write down the URL of your storage. 
2. This notebook uses the 'azure-storage-file-datalake' and the 'azure-identity' python packages. You need to install both packages to run this notebook. 

In the notebook you will see comments with `TODO`. In these cells you will need to add a name or variable to the code.

In [ ]:
%pip install azure-storage-file-datalake azure-identity

In [ ]:
# restart python to apply installed packages
dbutils.library.restartPython()

In [ ]:
# TODO: provide the sas token and the URL of your storage
account_url_full = "<put here your URL>"
# remove the folder from the url
account_url = account_url_full[:-20]
sas_token = "<put here your sas token>"
# the file system is fixed, this is the container SC Navigator will write its results
file_system="sc-navigator-export"

In [ ]:
# import required packages
import os
from azure.storage.filedatalake import (
    DataLakeServiceClient,
    DataLakeDirectoryClient,
    FileSystemClient
)
from azure.identity import DefaultAzureCredential

In [ ]:
# create a DataLakeServiceClient to access the storage 
dsc = DataLakeServiceClient(account_url=account_url, credential=sas_token)


In [ ]:
# list all available scenario's on the storage
# Note that you need to save the scenario from SCN with datalake storage enables before they will be visible!
file_system_client = dsc.get_file_system_client(file_system=file_system)
paths = file_system_client.get_paths()
list_of_scenarios = list()
for path in paths:
    if "/" not in path.name and path.name != "info.txt":
        print(path.name + '\n')
        list_of_scenarios.append(path.name)
    else:
        continue

In [ ]:
# the results are stored per scenario. You can change the list of scenario's to load if you change the list_of_scenarios variable.
# list_of_scenarios = ["<scenario_1>", "<scenario_2>"]
# this code creates a directory client per scenario to load its files
dictionary_of_scenario_clients = {}
for scenario in list_of_scenarios:
    client = dsc.get_directory_client(file_system=file_system,directory=scenario)
    dictionary_of_scenario_clients[scenario] = client

In [ ]:
# load the files for the selected scenario's
import io
import pandas as pd
from collections import defaultdict
results = defaultdict(list)
paths = file_system_client.get_paths()
for path in paths:
    if "/" in path.name:
        scenario = path.name.split("/")[0]
        file_name = path.name.split("/")[1]
        if scenario in list_of_scenarios:
            try:
                file = dictionary_of_scenario_clients[scenario].get_file_client(file_name)
                data_file = file.download_file()
                data_binary = data_file.readall()
                parquet_file = io.BytesIO(data_binary)
                df = pd.read_parquet(parquet_file)
                df["scenario_id"] = scenario
                results[file_name.split(".")[0]].append(df)
            except:
                print(file_name + " could not be loaded into a dataframe")

In [ ]:
# combine the list of dataframes into one dataframe per file type
dataframes_for_visualization = dict()
for k,v in results.items():
    df = pd.concat(v)
    dataframes_for_visualization[k] = df

In [ ]:
# show all data 
[k for k,v in dataframes_for_visualization.items()]

In [ ]:
# in this example we use the end-to-end-report only but other data can be processed in a similar manner
df_e2e = dataframes_for_visualization["end-to-end-report"]
display(df_e2e)

In [ ]:
# do some final post-processing so data can be stored as a hive_table
# spark cannot handle spaces or brackets 
import numpy as np
df_e2e.columns = [x.replace(" ", "_") for x in df_e2e.columns]
df_e2e.columns = [x.replace("(", "") for x in df_e2e.columns]
df_e2e.columns = [x.replace(")", "") for x in df_e2e.columns]
df_e2e = df_e2e.replace({None: np.nan})

In [ ]:
# save to databricks hive storage
# you can choose to use another destination for example csv files or a database
df_spark = spark.createDataFrame(df_e2e)
df_spark.write.saveAsTable("SC_Navigator_e2e")


## Remarks

With the table saved to hive or another destination you can load the data into PowerBI for visualization. 